In [70]:
import argparse
import json
from google.protobuf.json_format import MessageToDict
from data.chum import chumpy
import matplotlib.pyplot as plt
import numpy as np
from vehicle.common.proto.decision_pb2 import Decision

import bokeh.plotting as bp
import bokeh

bokeh.io.output_notebook()

#from bokeh.plotting import figure, output_file, show

Loading BokehJS ...

In [71]:
def parse_args():
    parser = argparse.ArgumentParser()

    parser.add_argument("--chum-uri", "-i", required=True, type=str,
            help="Chum URI to get data from")
    parser.add_argument("--outfile", "-o", required=True, type=str,
            help="Path to store data to")
    return parser.parse_args()

def read_decision(uri):
    "Prints out s position, velocity, and timing data"
    chum_store, chum_range = chumpy.parseChumUri(uri)
    chum_range.topics = {'/planner/decision'}

    reader = chumpy.Reader.create(chum_store, chum_range)

    out = {'ts' : [],
           'state' : [],
           's' : [],
           'ey' : [],
           'vx' : [],
           'vy' : [],
           'z' : [],
           'decision_traj' : [],
           'decision_state' : []}
    for msg in reader:
        decision = Decision()
        decision.ParseFromString(msg.getData())
        out['ts'] += [msg.message_publish_time_ns]
        out['state'] += [decision.state]
        out['s'] += [decision.route_stz.s]
        out['ey'] += [decision.route_stz.t]
        out['vx'] += [decision.hero_state.body_velocity.v_x]
        out['vy'] += [decision.hero_state.body_velocity.v_y]
        out['z'] += [decision.route_stz.z]
        out['decision_traj'] += [MessageToDict(decision.trajectory)]
        out['decision_state'] += [decision.state]
    return out

def state_val(key, traj):
    return [pt[key] for pt in traj['states']]
def control_val(key, traj):
    return [pt[key] for pt in traj['controls']]

In [72]:
# "test branch"
# uri1 = "chum://hero@12345.0-12376.0?i=$cache,/mnt/sun-pcs01/sim/pipeline/chum_cache,$vars,$empty,$default&v=logtests/PlannerModule/58d2df39146681246d2204fb023c3ff098ca3f01acdf0677fc4b0e6c179af723_30eff7ce968211eabd390242ac110003"
# "control branch"
# uri2 = "chum://hero@12345.0-12376.0?i=$cache,/mnt/sun-pcs01/sim/pipeline/chum_cache,$vars,$empty,$default&v=logtests/PlannerModule/2e0e58a718a85fdcf0d1d3cf72048e2d47822a441e8a2ef0dbcf10799b2c745b_a7bbb106969411eabee90242ac110009"

"test branch"
# uri1 = "chum://hero@12345.001001-12361.436001011?i=$empty,/tmp/chum&v=local_sim12111,local_sim12111"
# uri1 = "chum://hero@12345.001001-12361.436001011?i=$empty,/tmp/chum&v=local_sim27817,local_sim27817"
uri1 = "chum://hero@12345.001001-12361.436001011?i=$empty,/tmp/chum&v=local_sim20548,local_sim20548"
# uri1 = "chum://hero@12345.001001-12361.631001034?i=$empty,/tmp/chum&v=local_sim169,local_sim169"
uri1 = "chum://hero@12345.001001-12361.436001011?i=$empty,/tmp/chum&v=local_sim2479,local_sim2479"

"control branch"
uri2 = "chum://hero@12345.001001-12361.761001011?i=$empty,/tmp/chum&v=local_sim25986,local_sim25986"


"test branch"
uri1 = "chum://hero@12345.001001-12375.00600113?i=$empty,/tmp/chum&v=local_sim32203,local_sim32203"
"control branch"
uri2 = "chum://hero@12345.0-12376.0?i=$cache,/mnt/sun-pcs01/sim/pipeline/chum_cache,$vars,$empty,$default&v=logtests/PlannerModule/5efa3ef05de68f75fde4bcdb4cafd9345a77df1cb2389e3cc0070da011f09dcc_65c55be2968711ea82740242ac110008"

"highway initialization issue"
"test branch"
uri1 = "chum://kitt_sim@12345.0-12353.000000018?i=$cache,/mnt/sun-pcs01/sim/pipeline/chum_cache,$vars,$empty&v=logtests/PlannerModule/27e103ea7e152c3fef371155d0ff5f5b76ec761c51d2197161ae291f9b78ffde_9cca1d60a25511ea85a90242ac110004"
"control branch"
uri2 = "chum://kitt_sim@12345.0-12352.390000014?i=$cache,/mnt/sun-pcs01/sim/pipeline/chum_cache,$vars,$empty&v=logtests/PlannerModule/781def756ecdc0e43558a7700287b126637d11af71b8cc6ce4bf49cd00403561_64893bd8a38711eab5aa0242ac110005"
"blah"
uri2 = "chum://kitt_sim@12345.0-12352.655000035?i=$empty,/tmp/chum&v=local_sim32529,local_sim32529"

In [73]:
d1 = read_decision(uri1)
d2 = read_decision(uri2)

    

In [83]:
def plot_keys(fig, key1, key2, step):
    traj1 = d1['decision_traj'][step]
    traj2 = d2['decision_traj'][step]
    if key1 == 't':
        x_vals1 = traj1['times']
        x_vals2 = traj2['times']
    else:
        x_vals1 = state_val(key1, traj1)
        x_vals2 = state_val(key1, traj2)
    y_vals1 = state_val(key2, traj1)
    y_vals2 = state_val(key2, traj2)
    fig.multi_line([x_vals1, x_vals2], [y_vals1, y_vals2], line_width=2, color=['firebrick', 'navy'])

def plot_x_plus_y_vs_key(fig, key, step):
    traj1 = d1['decision_traj'][step]
    traj2 = d2['decision_traj'][step]
    x0 = state_val('x',traj1)[0]
    y0 = state_val('x',traj1)[0]
    x_vals1 = np.abs(np.array(state_val('x', traj1))-x0) + np.abs(np.array(state_val('y', traj1))-y0)
    x_vals2 = np.abs(np.array(state_val('x', traj2))-x0) + np.abs(np.array(state_val('y', traj2))-y0)
    if key == 'acc':
        x_vals1 = x_vals1[:-1]
        x_vals2 = x_vals2[:-1]
        y_vals1 = control_val(key, traj1)
        y_vals2 = control_val(key, traj2)
    else:
        y_vals1 = state_val(key, traj1)
        y_vals2 = state_val(key, traj2)
    print(step)
    print(y_vals1[:5])
    fig.multi_line([x_vals1, x_vals2], [y_vals1, y_vals2], line_width=[3,1], color=['tan', 'deepskyblue'])
    fig.circle(x_vals1, y_vals1, color='tan')
    fig.circle(x_vals2, y_vals2, color='deepskyblue')

def time_durations(step):
    times1 = d1['decision_traj'][step]['times']
    times2 = d2['decision_traj'][step]['times']
    return [times1[-1] - times1[0], times2[-1] - times2[0]]
    
# def plot_x_plus_y_vs_vx_seq(fig, step_start, step_end):
#     traj1 = d1['decision_traj'][step]
#     traj2 = d2['decision_traj'][step]
#     x_vals1 = np.array(state_val('x', traj1)) + np.array(state_val('y', traj1))
#     x_vals2 = np.array(state_val('x', traj2)) + np.array(state_val('y', traj2))
#     y_vals1 = state_val('vx', traj1)
#     y_vals2 = state_val('vx', traj2)
#     print(step)
#     fig.multi_line([x_vals1, x_vals2], [y_vals1, y_vals2], line_width=[4,2], color=['tan', 'deepskyblue'])
    
# step = 5
# print(d1['ts'][step] * 1e-9)
# print(d2['ts'][step] * 1e-9)
# fig1 = bp.figure(plot_width=400, plot_height=400)
# plot_keys(fig1, 'arcLength', 'vx', step)
# bp.show(fig1)
# fig2 = bp.figure(plot_width=400, plot_height=400)
# plot_keys(fig2, 'x', 'y', step)
# bp.show(fig2)

step = 5
key = 'yaw'
print(d1['ts'][step] * 1e-9)
print("decision state: {}".format(d1['decision_state'][step]))
print("decision state: {}".format(d2['decision_state'][step]))
fig = bp.figure(plot_width=400, plot_height=400)
plot_x_plus_y_vs_key(fig, key, step)
bp.show(fig)

# key = 'acc'
# print(d1['ts'][step] * 1e-9)
# print("decision state: {}".format(d1['decision_state'][step]))
# print("decision state: {}".format(d2['decision_state'][step]))
# fig = bp.figure(plot_width=400, plot_height=400)
# plot_x_plus_y_vs_key(fig, key, step)
# bp.show(fig)

step += 1
print(d1['ts'][step] * 1e-9)
print("decision state: {}".format(d1['decision_state'][step]))
print("decision state: {}".format(d2['decision_state'][step]))
fig = bp.figure(plot_width=400, plot_height=400)
plot_x_plus_y_vs_key(fig, key, step)
bp.show(fig)

step += 1
print(d1['ts'][step] * 1e-9)
print("decision state: {}".format(d1['decision_state'][step]))
print("decision state: {}".format(d2['decision_state'][step]))
fig = bp.figure(plot_width=400, plot_height=400)
plot_x_plus_y_vs_key(fig, key, step)
bp.show(fig)


12346.801005000001
decision state: 3
decision state: 3
5
[-2.4553458690643315, -2.455345869070733, -2.454747862776232, -2.453353761572577, -2.451635329558013]


12346.901005000002
decision state: 2
decision state: 2
6
[-2.4552617238590355, -2.4515658936656326, -2.4482908973566166, -2.4458360476057237, -2.444147075693258]


12347.001005
decision state: 2
decision state: 2
7
[-2.454188597046184, -2.4459310100004865, -2.4390214032386197, -2.434502601205877, -2.431972556845086]


In [63]:
step = 42 # initial slamming to avoid car
step = 66 # control branch starts going again
step = 5

print("durations {}".format(time_durations(step)))

key = 'yaw'
print(d1['ts'][step] * 1e-9)
fig = bp.figure(plot_width=400, plot_height=400)
plot_x_plus_y_vs_key(fig, key, step)
bp.show(fig)

key = 'vx'
print(d1['ts'][step] * 1e-9)
fig = bp.figure(plot_width=400, plot_height=400)
plot_x_plus_y_vs_key(fig, key, step)
bp.show(fig)

print((d1['ts'][-1] - d1['ts'][0])*1e-9)
print((d1['ts'][-1] - d1['ts'][0])*1e-9)

durations [8.20007673310647, 8.20007673310647]
12346.801005000001
5
[-2.4553458690643315, -2.455345869070733, -2.454747862776232, -2.453353761572577, -2.451635329558013]


12346.801005000001
5
[26.0, 26.0, 25.924485154219024, 25.823948985200516, 25.69806000593977]


6.6000000000000005
6.6000000000000005


In [26]:
d1['decision_traj'][step]['states']

[{'x': 3342.9258410636216,
  'y': 3151.060991752994,
  'z': 0.3702,
  'yaw': -2.454188597046184,
  'vx': 25.922847037554334,
  'wz': 0.08264906458100352,
  'steeringAngle': 0.008863161625012602,
  'arcLength': 0.0,
  's': 4.544363946423573,
  'ax': -0.4591450337024128,
  'covariance': {'rows': 2, 'cols': 2, 'data': [0.0, 0.0, 0.0, 0.0]}},
 {'x': 3340.9308597549148,
  'y': 3149.4093324494484,
  'z': 0.3702,
  'yaw': -2.4459310100004865,
  'vx': 25.876932534183926,
  'wz': 0.08250267669587777,
  'steeringAngle': 0.008863161625012602,
  'arcLength': 2.589988978596335,
  's': 7.135369835732067,
  'ax': -0.4591450337024128,
  'covariance': {'rows': 2, 'cols': 2, 'data': [0.0, 0.0, 0.0, 0.0]}},
 {'x': 3338.954239390872,
  'y': 3147.7467125224234,
  'z': 0.3702,
  'yaw': -2.4390214032386197,
  'vx': 25.76356166542564,
  'wz': 0.056409499151884,
  'steeringAngle': 0.006086754348676533,
  'arcLength': 5.172886506855595,
  's': 9.719402004107486,
  'ax': -1.1333255823088282,
  'covariance': {'ro